## Problem Statement:

This project showcases a RAG application or a skeleton for chatbot that searches and retrieves context from USCIS policy based on the question asked by user. I alsow anted to showcase how important retrieval is im RAG system. Hence, I have compared quantitavely and qualitatively both vector-only search retrieval and hybrid search retrieval. I have further delved deep into hybrid retrieval system by varying the weights of the retrievers to see their eeffect on the responses.



## Installations

In [1]:
pip install llama-index ollama llama-index-embeddings-huggingface llmsherpa llama-index-vector-stores-pinecone llama-index-llms-ollama llama-index-postprocessor-flag-embedding-reranker FlagEmbedding llama-index-retrievers-bm25 ragas llama-index-postprocessor-cohere-rerank



[notice] A new release of pip is available: 24.0 -> 24.2
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [2]:
from llama_index.core import VectorStoreIndex, SimpleDirectoryReader, Settings
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from llama_index.core import Document
from llmsherpa.readers import LayoutPDFReader
from llama_index.core import VectorStoreIndex
from llama_index.core.evaluation import RetrieverEvaluator
from llama_index.core.node_parser import SimpleNodeParser
from llama_index.core.evaluation import generate_question_context_pairs



from dotenv import load_dotenv
load_dotenv('/Users/divyahegde/Documents/LLM/Final Project/.env') # LlamaCloud API Key
from llama_parse import LlamaParse


In [3]:
from pinecone import Pinecone
from pinecone import ServerlessSpec
from llama_index.vector_stores.pinecone import PineconeVectorStore
from llama_index.core import StorageContext
import os

Settings.chunk_size = 1024
Settings.chunk_overlap = 50
 
pc_api_key = os.environ['PINECONE_API_KEY']
pc = Pinecone(api_key = pc_api_key)  #os.getenv('PINECONE_API_KEY')

#pinecone_index = pc.Index("test")
pinecone_index = pc.Index("hybrid-search-visa-wise2")

vector_store = PineconeVectorStore(pinecone_index=pinecone_index)
storage_context = StorageContext.from_defaults(vector_store=vector_store)

### Reading the policy and chunking the documents

In [4]:
documents = SimpleDirectoryReader(input_dir = "/Users/divyahegde/Documents/LLM/Final Project/uscis_new 2").load_data(num_workers=4, show_progress = True)
documents

/Users/divyahegde/anaconda3/lib/python3.10/site-packages/pypdf/_crypt_providers/_cryptography.py:32: CryptographyDeprecationWarning: ARC4 has been moved to cryptography.hazmat.decrepit.ciphers.algorithms.ARC4 and will be removed from this module in 48.0.0.
  from cryptography.hazmat.primitives.ciphers.algorithms import AES, ARC4
/Users/divyahegde/anaconda3/lib/python3.10/site-packages/pypdf/_crypt_providers/_cryptography.py:32: CryptographyDeprecationWarning: ARC4 has been moved to cryptography.hazmat.decrepit.ciphers.algorithms.ARC4 and will be removed from this module in 48.0.0.
  from cryptography.hazmat.primitives.ciphers.algorithms import AES, ARC4
/Users/divyahegde/anaconda3/lib/python3.10/site-packages/pypdf/_crypt_providers/_cryptography.py:32: CryptographyDeprecationWarning: ARC4 has been moved to cryptography.hazmat.decrepit.ciphers.algorithms.ARC4 and will be removed from this module in 48.0.0.
  from cryptography.hazmat.primitives.ciphers.algorithms import AES, ARC4
/Users/

[Document(id_='fd7ee008-0d98-414f-8b3f-2bfc63f3fe3c', embedding=None, metadata={'page_label': '1', 'file_name': 'All Forms _ USCIS.pdf', 'file_path': '/Users/divyahegde/Documents/LLM/Final Project/uscis_new 2/All Forms _ USCIS.pdf', 'file_type': 'application/pdf', 'file_size': 484729, 'creation_date': '2024-08-03', 'last_modified_date': '2024-08-01'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={}, text="Skip to main content\nU.S. ﬂag\nAn ofﬁcial website of the United States government\xa0 \xa0\xa0 Here's how you know\nEspañol\nMultilingual Resources\nOfﬁcial Government Website\nOfﬁcial websites use .gov\nA .gov website belongs to an ofﬁcial government or ganization in the United States.\nSecure Website\nSecur e .gov websites use HTTPS\nA lock (  ) or https://

In [5]:
from llama_index.core.node_parser import SentenceSplitter

# initialize node parser
splitter = SentenceSplitter(chunk_size=1024)

nodes = splitter.get_nodes_from_documents(documents)

In [6]:
import torch
import os

#Load an Embedding Model from HuggingFace
Settings.embed_model = HuggingFaceEmbedding(
    model_name = "BAAI/bge-base-en-v1.5" #768 Embedding Dimension
)

In [7]:
#Getting the Vectors from Pinecone DB - Do this if the Pinecone Index already has vectors

index = VectorStoreIndex.from_vector_store(vector_store=vector_store, embed_model = Settings.embed_model)

In [8]:
from llama_index.llms.ollama import Ollama

Settings.llm = Ollama(model="llama3:instruct", request_timeout=360.0)


In [9]:
#structured_answer_filtering=True ensures that the Response Synthesizer is able to filter out any input nodes that are not relevant to the question being asked.
#response_mode = 'compact'
#qa_prompt creates a custom prompt template and answers the 

from llama_index.core.retrievers import VectorIndexRetriever
from llama_index.core import get_response_synthesizer
from llama_index.core import PromptTemplate
from llama_index.retrievers.bm25 import BM25Retriever
from llama_index.core.retrievers import QueryFusionRetriever
import Stemmer

qa_prompt = PromptTemplate(
    # "Context information is below.\n"
    # "---------------------\n"
    "You are a USCIS policy helper\n." 
    "You will be provided with a query about USCIS policies and guidelines and you must answer it clearly and provide detailed steps using only the context information and not any prior knowledge\n." 
    "If the steps need to follow a certain order then ensure that the order is stated clearly. If any mathematical calculations need to be done make sure to show them clearly. If any forms need to be filed, make sure to specify what those forms are. Also cite any actual URLs if required to provide more clarity and make sure that these URLs are not broken.\n"
    "Context information is below.\n"
    "---------------------\n"
    "{context_str}"
    "---------------------\n"
    "Given the context information and not prior knowledge, answer the query"
    "Query: {query_str}\n"
    "Answer: "
)

'''vector_retriever = VectorIndexRetriever(
    index=index,
    similarity_top_k = 8,
    embed_model = Settings.embed_model
)

##added fpor fusion
bm25_retriever = BM25Retriever.from_defaults(
    nodes=nodes,
    similarity_top_k=8,
    # Optional: We can pass in the stemmer and set the language for stopwords
    # This is important for removing stopwords and stemming the query + text
    # The default is english for both
    stemmer=Stemmer.Stemmer("english"),
    language="english"
)

retriever = QueryFusionRetriever(
   [vector_retriever, bm25_retriever],
    similarity_top_k=8,
    num_queries=1,  # set this to 1 to disable query generation
    mode="reciprocal_rerank",
    use_async=True,
    verbose=True,
    query_gen_prompt=qa_prompt,  # we could override the query generation prompt here
    retriever_weights = [0.2,0.8]
) '''

response_synthesizer = get_response_synthesizer(response_mode = "compact", llm = Settings.llm, text_qa_template = qa_prompt)

In [10]:
from IPython.display import display, Markdown
from llama_index.core.query_engine import RetrieverQueryEngine


In [11]:
import nest_asyncio

nest_asyncio.apply()

In [12]:
#response = query_engine.query('''I'm a F1 student and I'm going through an economic crisis. Can I take an off-campus employment to support myself and is it illegal to do so?''')
#display(Markdown(response.response))


When embeddings of larger dimensions are used (i.e. 1024) it takes a long time to create and upsert the embeddings and during retreival and reranking, the vectors are more sparse and hence it becomes difficult to find similar vectors and rerank them

## Generating responses using vector-search only and hybrid search with varying weights

In [13]:
from tqdm import tqdm 
from llama_index.llms.ollama import Ollama
from IPython.display import display, Markdown
from llama_index.core.query_engine import RetrieverQueryEngine
import pandas as pd 

df = pd.read_csv("/Users/divyahegde/Documents/LLM/Final Project/VisaWise Questions - Context based.csv")

df_questions = pd.DataFrame(df['Question'])


vector_retriever = VectorIndexRetriever(
    index=index,
    similarity_top_k = 8,
    embed_model = Settings.embed_model
)

query_engine_vector = RetrieverQueryEngine(
    retriever=vector_retriever,
    response_synthesizer=response_synthesizer,
    #node_postprocessors = [rerank]
)

##added fpor fusion
bm25_retriever = BM25Retriever.from_defaults(
    nodes=nodes,
    similarity_top_k=4,
    # Optional: We can pass in the stemmer and set the language for stopwords
    # This is important for removing stopwords and stemming the query + text
    # The default is english for both
    stemmer=Stemmer.Stemmer("english"),
    language="english"
)

retriever = QueryFusionRetriever(
   [vector_retriever, bm25_retriever],
    similarity_top_k=8,
    num_queries=1,  # set this to 1 to disable query generation
    mode="reciprocal_rerank",
    use_async=True,
    verbose=True,
    query_gen_prompt=qa_prompt,  # we could override the query generation prompt here
    retriever_weights = [0.6,0.4]
)

query_engine = RetrieverQueryEngine(
    retriever=retriever,
    response_synthesizer=response_synthesizer
    #node_postprocessors = [rerank]
)


In [14]:
from datasets import Dataset

dataset_questions = Dataset.from_pandas(df_questions)

In [15]:

for i in range(len(df_questions)):
    message = df_questions.loc[i, 'Question']
    df_questions.loc[i, 'rag_response_hybrid'] = query_engine.query(message).response 
    df_questions.loc[i, 'rag_response_vec'] = query_engine_vector.query(message).response
    

In [16]:
df_questions.to_csv('responses_evaluation.csv')

In [17]:
from ragas.testset.generator import TestsetGenerator
from ragas.testset.evolutions import simple, reasoning, multi_context
from llama_index.llms.openai import OpenAI
from llama_index.embeddings.openai import OpenAIEmbedding
import os

# generator with openai models
generator_llm = Settings.llm

critic_llm = Ollama(model="mistral-nemo")
embeddings = Settings.embed_model

generator = TestsetGenerator.from_llama_index(
    generator_llm=generator_llm,
    critic_llm=critic_llm,
    embeddings=embeddings,
)


In [18]:
documents_test = SimpleDirectoryReader(input_dir = "/Users/divyahegde/Documents/LLM/Final Project/uscis_new 2/test_set_folder").load_data()
documents_test

/Users/divyahegde/anaconda3/lib/python3.10/site-packages/pypdf/_crypt_providers/_cryptography.py:32: CryptographyDeprecationWarning: ARC4 has been moved to cryptography.hazmat.decrepit.ciphers.algorithms.ARC4 and will be removed from this module in 48.0.0.
  from cryptography.hazmat.primitives.ciphers.algorithms import AES, ARC4


[Document(id_='289e05ea-e38d-4991-a9d0-92bab77370f1', embedding=None, metadata={'page_label': '1', 'file_name': 'Employment Authorization for Certain H-4 Dependent Spouses _ USCIS.pdf', 'file_path': '/Users/divyahegde/Documents/LLM/Final Project/uscis_new 2/test_set_folder/Employment Authorization for Certain H-4 Dependent Spouses _ USCIS.pdf', 'file_type': 'application/pdf', 'file_size': 200615, 'creation_date': '2024-08-03', 'last_modified_date': '2024-08-01'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={}, text='Home> Working in the United States> Temporary Workers> H-1B Specialty Occupations>\nEmployment Authorization for Certain H-4 Dependent Spouses\nEmployme nt Authorization for Certain H-4\nDependent Spouses\nCertain H-4 dependent spouses of H-1B noni

In [19]:
#Syntethically generates questions based on the documents provided. Here I'm giving policies related to non-immigrant status student 

testset = generator.generate_with_llamaindex_docs(
    documents_test,
    test_size=5,
    distributions={simple: 0.5, reasoning: 0.25, multi_context: 0.25},
) 

embedding nodes:   0%|          | 0/132 [00:00<?, ?it/s]

Filename and doc_id are the same for all nodes.


Generating:   0%|          | 0/5 [00:00<?, ?it/s]

max retries exceeded for MultiContextEvolution(generator_llm=LlamaIndexLLMWrapper(run_config=RunConfig(timeout=60, max_retries=15, max_wait=90, max_workers=16, thread_timeout=80.0, exception_types=(<class 'Exception'>,), log_tenacity=False)), docstore=InMemoryDocumentStore(splitter=<langchain_text_splitters.base.TokenTextSplitter object at 0x1792ac190>, nodes=[Node(metadata={'page_label': '1', 'file_name': 'Employment Authorization for Certain H-4 Dependent Spouses _ USCIS.pdf', 'file_path': '/Users/divyahegde/Documents/LLM/Final Project/uscis_new 2/test_set_folder/Employment Authorization for Certain H-4 Dependent Spouses _ USCIS.pdf', 'file_type': 'application/pdf', 'file_size': 200615, 'creation_date': '2024-08-03', 'last_modified_date': '2024-08-01'}, page_content='Home> Working in the United States> Temporary Workers> H-1B Specialty Occupations>\nEmployment Authorization for Certain H-4 Dependent Spouses\nEmployme nt Authorization for Certain H-4\nDependent Spouses\nCertain H-4 de

In [20]:
import pickle 
with open('test_questions_dataset.pkl', 'wb') as f:  # open a text file
    pickle.dump(testset, f) # serialize the list 

In [21]:
with open('test_questions_dataset.pkl', 'rb') as f:
    testset = pickle.load(f)

In [22]:
test_df = testset.to_pandas()
test_df

question  \
0  Here is a question that can be fully answered ...   
1  Here is the question that can be fully answere...   
2  What changes did USCIS make since 2021 to ease...   
3  Here is a question that can be fully answered ...   

                                            contexts  \
0  [point, to maintain nonimmigrant status your c...   
1  [ALERT: On March 25, USCIS launched online fi...   
2  [point, to maintain nonimmigrant status your c...   
3  [“bundling” forms I-129 and I-539 for certain ...   

                                        ground_truth evolution_type  \
0  USCIS has taken several actions to support H-1...         simple   
1  H-1B beneficiaries who wish to change employer...         simple   
2  USCIS has taken several actions since 2021 to ...      reasoning   
3  USCIS has announced several process enhancemen...         simple   

                                            metadata  episode_done  
0  [{'page_label': '17', 'file_name': 'FAQs for I...          True  
1  [{'page_label': '2', 'file_name': 'H-1B Specia...          True  
2  [{'page_label': '17', 'file_name': 'FAQs for I...          True  
3  [{'page_label': '18', 'file_name': 'FAQs for I...          True

In [23]:
test_df.to_csv('Test set from RAGAS.csv')

In [24]:
#defining ragas metrics

from ragas.metrics import (
    faithfulness,
    answer_relevancy,
    context_precision,
    context_recall,
)
from ragas.metrics.critique import harmfulness

metrics = [
    faithfulness,
    answer_relevancy,
    context_precision,
    context_recall,
    harmfulness,
]

In [25]:
ds = testset.to_dataset()

ds_dict = ds.to_dict()
ds_dict["question"]
ds_dict["ground_truth"]

['USCIS has taken several actions to support H-1B nonimmigrants seeking adjustment or change of status in the United States, including issuing an unprecedented number of employment-based green cards in fiscal years 2022 and 2023, increasing the maximum validity period of Employment Authorization Documents (EADs) to 5 years for adjustment of status applicants and bringing back “combo cards” that provide evidence of both employment authorization and advance parole. Additionally, they have expanded premium processing to all filers of Form I-140, Immigrant Petition for Noncitizen Workers, as well as certain filers of Form I-765, Application for Employment Authorization, and Form I-539, Application to Extend/Change Nonimmigrant Status. Furthermore, the agency has updated policy guidance on expedite requests, including when USCIS may expedite adjudication of an Application for Travel Document (Form I-131) when an applicant demonstrates a pressing or critical need to leave the United States, 

In [26]:
evaluator_llm = Ollama(model="llama3.1", request_timeout=360.0)

## for different weights in hybrid retreiever and with COHERE reranking model

In [ ]:
from llama_index.postprocessor.cohere_rerank import CohereRerank

reranker = CohereRerank(api_key=os.getenv('COHERE_API_KEY'), top_n=4)

In [ ]:
weights = [0.0,0.2,0.4,0.6,0.8,1]

for i in range(len(weights)):
    retriever = QueryFusionRetriever(
        [vector_retriever, bm25_retriever],
        similarity_top_k=8,
        num_queries=1,  # set this to 1 to disable query generation
        use_async=True,
        verbose=True,
        query_gen_prompt=qa_prompt,  # we could override the query generation prompt here
        retriever_weights = [weights[i],1-weights[i]]
    )
    query_engine = RetrieverQueryEngine(
    retriever=retriever,
    response_synthesizer=response_synthesizer,
    node_postprocessors = [reranker]
    )
    
    result = evaluate(
    query_engine=query_engine,
    metrics=metrics,
    dataset=ds_dict,
    #llm=Settings.llm,
    embeddings=Settings.embed_model,
    raise_exceptions=False,
    #run_config=RunConfig(max_retries=3, max_wait=20)
    )

    print('Results for '+ str(weights[i])+ ' : ', result)

    

As we can observe, the answer_relevancy is the highest for 60% weightage to vector search and 40% to BM25 keyword retriever

## Context-based questions for qualitative analysis

In [ ]:
df_context_based_questions = pd.read_csv('/Users/divyahegde/Documents/LLM/Final Project/VisaWise Questions - Context based.csv')

In [ ]:
df_context_based_questions = pd.DataFrame(df_context_based_questions['Question'][1:3]) 

In [ ]:
df_context_based_questions = df_context_based_questions['Question'].reset_index()

In [ ]:
weights = [0.0,0.2,0.4,0.6,0.8,1]
results_df = pd.DataFrame(columns=['Question','weight','response'])
count = 0

for i in range(len(weights)):
    for q in range(len(df_context_based_questions)):
        retriever = QueryFusionRetriever(
            [vector_retriever, bm25_retriever],
            similarity_top_k=8,
            num_queries=1,  # set this to 1 to disable query generation
            use_async=True,
            verbose=True,
            query_gen_prompt=qa_prompt,  # we could override the query generation prompt here
            retriever_weights = [weights[i],1-weights[i]]
        )
        query_engine = RetrieverQueryEngine(
        retriever=retriever,
        response_synthesizer=response_synthesizer,
        node_postprocessors = [reranker]
        )
        
        result = evaluate(
        query_engine=query_engine,
        metrics=metrics,
        dataset=ds_dict,
        #llm=Settings.llm,
        embeddings=Settings.embed_model,
        raise_exceptions=False,
        #run_config=RunConfig(max_retries=3, max_wait=20)
        )



        response = query_engine.query(df_context_based_questions['Question'][q])
        #display(Markdown(response.response))
        count = count + 1 
        
        temp_df = pd.DataFrame(
            {
                'Question' : df_context_based_questions['Question'][q],
                'weight' : i,
                'response' : response.response
            } , index = [count]
        )

        results_df = pd.concat([results_df,temp_df])


In [ ]:
results_df['response']

In [ ]:
results_df.to_csv('Weights tuning responses.csv')

In [ ]:
results_df = pd.read_csv('Weights tuning responses.csv')
results_df.columns

In [ ]:
results_df['Question']

## Lets look at the response for different weights 

#### Q1 - I'm on a dependant visa. Will enrolling myself into a university require a F1 visa?

In [ ]:
results_df_q1 = results_df[results_df['Question'] == 'I\'m on a dependant visa. Will enrolling myself into a university require a F1 visa?']
results_df_q1.drop(columns = ['Unnamed: 0'], inplace=True)

In [ ]:
pd.set_option('display.max_colwidth', None)

In [ ]:
results_df_q1 
## weight column corresponds to the indices of weights value. So weight 0 is 0.0, weight 1 is 0.2, and so on..

Comparing the results, most responses give the gist of what is to be expected and what is to be done. But if you closely observe, if you assign more weightage to keyword based (weight 0), itseems to be mixing up some context. Nowhere in the question have I mentioned that the dependant is depedent on F1 visa holder. This is becuase keyword retrieval is focusing on dependant and F1 visa.

The responses for weights 0.6 and 0.8 seem the best (although 0.8 does seem to assume the same thing as weight 0.0 did). They seem to strike a balance between answering to the point, showing references, and further steps that can be taken.

## Evaluating with the help of another LLM

In [ ]:
import openai
import pandas as pd
import os

openai.api_key = os.environ.get('OPENAI_API_KEY')


In [ ]:
#Load the Responses
df = pd.read_csv("/Users/divyahegde/Documents/LLM/Final Project/responses_evaluation.csv")
df.head()

In [ ]:
from openai import OpenAI

client = OpenAI(api_key = openai.api_key)

In [ ]:
#Define Function for Scoring the Responses
import re

def evaluate_response(question, ground_truth, llm_only_response, rag_response):
    prompt = f"""
    Question: {question}
    Ground Truth: {ground_truth}
    LLM Only Response: {llm_only_response}
    RAG Response: {rag_response}

    Compare the LLM only response and the RAG response to the ground truth respectively on the following criteria:
    - Relevance: Does the response directly address the query?
    - Accuracy: Is the information provided correct?
    - Completeness: Does the response cover all necessary aspects of the query?
    - Clarity: Is the response easy to understand?
    - Conciseness: Is the response free from unnecessary information?

    Thereafter, provide an overall score out of 10 for LLM Only Response and for the RAG Response respectively. Do not change the format of the output.

    ### Summary
    - LLM Only Response:

    - RAG Response:

    ### LLM Only Overall Score:
    ### RAG Overall Score:
    """

    response = client.chat.completions.create(
  model="gpt-4o-mini",
  messages=[
    {"role": "system", "content": "You are a helpful assistant that evaluates responses"},
    {"role": "user", "content": prompt}
  ]
)

    s = response.choices[0].message.content
    print(s)

    llm_only_score = re.search(r'LLM Only Overall Score: (\d+)', s).group(1).strip()
    rag_score = re.search(r'RAG Overall Score: (\d+)', s).group(1).strip()

    return int(llm_only_score), int(rag_score)


In [ ]:
from tqdm import tqdm

for i in tqdm(range(len(df))):
  df.loc[i, 'llm_only_score'], df.loc[i, 'rag_score'] = evaluate_response(df.loc[i, 'question'],
                                                                 df.loc[i, 'ground_truth'],
                                                                 df.loc[i, 'llm_only_response'],
                                                                 df.loc[i, 'rag_response'])

In [ ]:
import numpy as np

df['llm_only_score'] = np.where(df['llm_only_score'] > 10, 10*df['llm_only_score']/50, df['llm_only_score'])
df['rag_score'] =  np.where(df['rag_score'] > 10, 10*df['rag_score']/50, df['rag_score'])

In [ ]:
print(f"Avg. LLM Only Score: {df['llm_only_score'].mean()}")
print(f"Avg. RAG Score: {df['rag_score'].mean()}")

## COnclusion

RAG applications are really helpful in cases where the LLM has no access to private information or is not trained on some documents. RAG applications have use cases in most domains where there are multiple documents involved or the knowledge base keeps getting updated. 

As orchestrated above, it is important to strike a balance between keyword-based search and vector-based search. This could be done by manually looking over the responses generated or via calculation of metrics like MRR, hit rate, or evaluating using frameworks like RAGAS.

